# Spatially Joins the Hex2Vec Table to Amazon Stops


In [1]:
import os
import sys

# hex2vec
sys.path.insert(0, "/Users/max/Development/green-last-mile/hex2vec")

# sys.path.append(os.path.join("", "amazon-routing-challenge"))


In [2]:
import json
import pandas as pd
import geopandas as gpd
import h3

# import from hex2vec
from src.data.make_dataset import h3_to_polygon


## Define File Paths


In [3]:
hexagon_size = 9
route_file = (
    "./data/almrrc2021-data-training/model_build_inputs/route_df_merged_augmented.pkl"
)

boston_tag_counts = (
    lambda x: f"~/Desktop/osmnx-cities/hexed-complete/Boston, MA/{x}.pkl"
)

# boston_hexagon_file = boston_hexagons(9)
boston_tag_count_file = boston_tag_counts(9)


## Open the Hexagons


In [4]:
tag_df = pd.read_pickle(boston_tag_count_file).reset_index()


In [5]:
tag_df.head()


h3  amenity_arts_centre  amenity_atm  amenity_bank  \
0  892a33d9357ffff                    0            0             0   
1  892a33d9a13ffff                    0            0             0   
2  892a33d956fffff                    0            0             0   
3  892a33db397ffff                    0            0             0   
4  892a33da997ffff                    0            0             0   

   amenity_bar  amenity_bbq  amenity_bench  amenity_bicycle_parking  \
0            0            0              0                        0   
1            0            0              0                        0   
2            0            0              0                        0   
3            0            0              0                        0   
4            0            0              0                        0   

   amenity_bicycle_repair_station  amenity_cafe  ...  waterway_tidal_channel  \
0                               0             0  ...                       0   
1                               0             0  ...                       0   
2                               0             0  ...                       0   
3                               0             0  ...                       0   
4                               0             0  ...                       0   

   waterway_ditch  waterway_pressurised  waterway_fairway  waterway_boatyard  \
0               0                     0                 0                  0   
1               0                     0                 0                  0   
2               0                     0                 0                  0   
3               0                     0                 0                  0   
4               0                     0                 0                  0   

   waterway_lock_gate  waterway_soakhole  waterway_turning_point  \
0                   0                  0                       0   
1                   0                  0                       0   
2                   0                  0                       0   
3                   0                  0                       0   
4                   0                  0                       0   

   waterway_water_point  waterway_fuel  
0                     0              0  
1                     0              0  
2                     0              0  
3                     0              0  
4                     0              0  

[5 rows x 971 columns]

## Open the Route Dataframe


In [6]:
route_df = pd.read_pickle(route_file)


In [7]:
route_df


depth  executor_capacity_cm3 has_time_window     height  \
0       34.157143              3313071.0           False  12.871429   
1       30.500000              3313071.0           False  10.200000   
2       29.700000              3313071.0           False   6.350000   
3       37.450000              3313071.0           False  10.150000   
4       32.866667              3313071.0            True   9.900000   
...           ...                    ...             ...        ...   
898410  34.300000              4247527.0           False  11.400000   
898411  32.650000              4247527.0           False   6.100000   
898412  34.300000              4247527.0           False   7.600000   
898413  29.200000              4247527.0           False  16.500000   
898414  25.200000              4247527.0           False  11.600000   

              lat         lng  package_id  planned_service_time  \
0       34.088467 -118.284521         7.0                 184.8   
1       34.088709 -118.284839         1.0                  34.0   
2       34.088717 -118.286484         2.0                 145.0   
3       34.089727 -118.285530         2.0                  90.0   
4       34.090901 -118.284257         3.0                 254.1   
...           ...         ...         ...                   ...   
898410  42.201350  -88.390206         1.0                  51.0   
898411  42.202126  -88.389695         4.0                 176.0   
898412  42.201465  -88.379400         1.0                  55.0   
898413  42.202375  -88.379400         2.0                 109.0   
898414  42.194055  -88.392591         2.0                 113.0   

                                            route_id route_score station_code  \
0       RouteID_00143bdd-0a6b-49ec-bb35-36593d303e77        High         DLA3   
1       RouteID_00143bdd-0a6b-49ec-bb35-36593d303e77        High         DLA3   
2       RouteID_00143bdd-0a6b-49ec-bb35-36593d303e77        High         DLA3   
3       RouteID_00143bdd-0a6b-49ec-bb35-36593d303e77        High         DLA3   
4       RouteID_00143bdd-0a6b-49ec-bb35-36593d303e77        High         DLA3   
...                                              ...         ...          ...   
898410  RouteID_fffd257c-3041-4736-be7a-5efea8af1173      Medium         DCH4   
898411  RouteID_fffd257c-3041-4736-be7a-5efea8af1173      Medium         DCH4   
898412  RouteID_fffd257c-3041-4736-be7a-5efea8af1173      Medium         DCH4   
898413  RouteID_fffd257c-3041-4736-be7a-5efea8af1173      Medium         DCH4   
898414  RouteID_fffd257c-3041-4736-be7a-5efea8af1173      Medium         DCH4   

       stop_id  time_of_day     type      volume      width  
0           TG      41566.0  Dropoff  107970.047  25.342857  
1           GP      41617.0  Dropoff    5942.010  19.100000  
2           HT      41798.0  Dropoff    8010.523  18.800000  
3           AG      41977.0  Dropoff   19134.644  26.700000  
4           QM      42297.0  Dropoff   21141.936  22.700000  
...        ...          ...      ...         ...        ...  
898410      WT      62632.0  Dropoff   10440.234  26.700000  
898411      XJ      62852.0  Dropoff   15428.872  19.625000  
898412      NX      63114.0  Dropoff    6282.388  24.100000  
898413      JN      63237.0  Dropoff   23628.254  22.250000  
898414      DE      63672.0  Dropoff   14306.432  23.950000  

[898415 rows x 16 columns]

# Filter only Boston


In [8]:
route_df = route_df.loc[route_df.station_code.str.contains("BO")].reset_index()


### Create Geodataframe


In [9]:
route_df = gpd.GeoDataFrame(
    data=route_df,
    geometry=gpd.points_from_xy(x=route_df.lng, y=route_df.lat, crs="EPSG:4326"),
)


## Merge the Dataframes


In [10]:
route_df["h3"] = route_df.geometry.apply(lambda x: h3.geo_to_h3(x.y, x.x, hexagon_size))
# route_df = route_df.merge(tag_df, on='h3', how='inner')
# route_df.reset_index(inplace=True, drop=True)
# route_df.drop(columns=['index'], inplace=True)


## NN Playground


In [11]:
TOP_LEVEL_OSM_TAGS = [
    # "aerialway",
    # "aeroway",
    "amenity",
    # "barrier",
    # "boundary",
    "building",
    "craft",
    # "emergency",
    # "geological",
    "healthcare",
    "highway",
    # "historic",
    "landuse",
    "leisure",
    "man_made",
    # "military",
    "natural",
    "office",
    "place",
    # "power",
    "public_transport",
    "railway",
    "route",
    "shop",
    "sport",
    "telecom",
    "tourism",
    "water",
    "waterway",
]


In [12]:
from pathlib import Path
import h3
from src.nearest_neighbor.nearest_neighbor import NearestNeighbor
from src.data.load_data import load_city_tag
from shapely.geometry import Point


In [13]:
nn = NearestNeighbor(
    Path("/Users/max/Desktop/osmnx-cities/hexed-raw/Boston, MA"),
    Path("/Users/max/Development/green-last-mile/hex2vec/filters/from_wiki.json"),
    50,
    TOP_LEVEL_OSM_TAGS,
)


In [14]:
route_df = nn.prepare_df_apply(route_df)
groupbyer = route_df.groupby("h3_5")
traversal_order = nn.get_traversal_order(route_df.geometry, route_df["h3_5"].unique())


In [16]:
dfs = [nn.count_tags(groupbyer.get_group(hex)) for hex in traversal_order]

# for hex in ["852a302ffffffff", "852a315bfffffff"]:
#     nn.count_tags(groupbyer.get_group(hex))

852a339bfffffff
852a3067fffffff
852a3063fffffff
852a3073fffffff
852a3077fffffff
852a302bfffffff
852a3393fffffff
852a3397fffffff
852a315bfffffff
852a3143fffffff needed but not in files. Pulling from API
running for hex 852a3143fffffff
amenity already exists
building already exists
craft already exists
healthcare already exists
highway already exists
852a302ffffffff
852a33abfffffff
852a33affffffff needed but not in files. Pulling from API
running for hex 852a33affffffff
852a3307fffffff needed but not in files. Pulling from API
running for hex 852a3307fffffff
852a33a3fffffff needed but not in files. Pulling from API
running for hex 852a33a3fffffff
852a3333fffffff needed but not in files. Pulling from API
running for hex 852a3333fffffff
852a3317fffffff
852a338ffffffff
852a3313fffffff
852a331bfffffff
852a330bfffffff needed but not in files. Pulling from API
running for hex 852a330bfffffff
852a3357fffffff needed but not in files. Pulling from API
running for hex 852a3357fffffff
852a33cffffff

In [17]:
new_df = pd.concat(dfs, axis=0)

### Convert Tags to int

In [18]:
new_df[[c for c in nn._tag_columns if c in new_df.columns]].max().max()


481.0

In [19]:
new_df[new_df.columns.intersection(nn._tag_columns)] = new_df[new_df.columns.intersection(nn._tag_columns)].fillna(0).astype("Int16")

### Drop All Zero Columns

In [22]:

# drop all tag columns that are all 0
new_df.drop(new_df.columns.intersection(nn._tag_columns)[~new_df[new_df.columns.intersection(nn._tag_columns)].any(axis=0)], axis=1, inplace=True)

In [23]:
new_df.shape

(139693, 501)

### Drop all the Geometry columns

In [24]:
new_df.to_pickle(
    "/Users/max/Desktop/osmnx-cities/hexed-complete/Boston, MA/joined_route_tags_50m.pkl",
    protocol=4,
)

In [73]:
len(set(hexed_routes.columns)), len(hexed_routes.columns)


(582, 582)

In [59]:
# tag_df.head()


## Merge the Route DataFrame with the Tag Counts


In [10]:
tag_columns = tag_df.columns.difference(["h3"])


In [43]:
# print([col for col in hexed_routes.columns if "building" in col])
# print(tag_columns)


### Drop Data with Missing Features


In [36]:
# # keep track of package volume
# package_df["volume"] = package_df["width"] * package_df["depth"] * package_df["height"]

# # check if package has a window
# package_df["has_window"] = (
#     ~package_df["time_window_start"].isna() & ~package_df["time_window_end"].isna()
# )

# # this isn't the most efficient way to do this but :shrug:
# package_feature_df = (
#     package_df.set_index(
#         ["route_id", "stop_id", "package_id"],
#     )
#     .merge(
#         hexed_routes.set_index(["route_id", "stop_id"]),
#         left_index=True,
#         right_index=True,
#     )
#     .reset_index()
# )

# package_feature_df["city"] = package_feature_df["station_code"].str[1:-1]
# package_feature_df["city_zone"] = (
#     package_feature_df["station_code"] + "~" + package_feature_df["zone_id"]
# )

# package_feature_df.time_window_start = pd.to_datetime(
#     package_feature_df.time_window_start
# )
# package_feature_df.time_window_end = pd.to_datetime(package_feature_df.time_window_end)
# package_feature_df.departure_datetime = pd.to_datetime(
#     package_feature_df.departure_datetime
# )


In [46]:
# package_feature_df.head()


In [22]:
# package_feature_df[tag_columns].head()


amenity_animal_boarding  amenity_animal_breeding  amenity_animal_shelter  \
0                        0                        0                       0   
1                        0                        0                       0   
2                        0                        0                       0   
3                        0                        0                       0   
4                        0                        0                       0   

   amenity_arts_centre  amenity_atm  amenity_baby_hatch  amenity_baking_oven  \
0                    0            0                   0                    0   
1                    0            0                   0                    0   
2                    0            0                   0                    0   
3                    0            0                   0                    0   
4                    0            0                   0                    0   

   amenity_bank  amenity_bar  amenity_bbq  ...  waterway_pressurised  \
0             0            0            0  ...                     0   
1             0            0            0  ...                     0   
2             0            0            0  ...                     0   
3             0            0            0  ...                     0   
4             0            0            0  ...                     0   

   waterway_river  waterway_riverbank  waterway_soakhole  waterway_stream  \
0               0                   0                  0                0   
1               0                   0                  0                0   
2               0                   0                  0                0   
3               0                   0                  0                0   
4               0                   0                  0                2   

   waterway_tidal_channel  waterway_turning_point  waterway_water_point  \
0                       0                       0                     0   
1                       0                       0                     0   
2                       0                       0                     0   
3                       0                       0                     0   
4                       0                       0                     0   

   waterway_waterfall  waterway_weir  
0                   0              0  
1                   0              0  
2                   0              0  
3                   0              0  
4                   0              0  

[5 rows x 970 columns]

In [11]:
route_df[route_df.columns.difference(tag_columns)].head()


depth  executor_capacity_cm3                    geometry               h3  \
0   32.5              3313071.0  POINT (-71.21077 42.24904)  892a339a2dbffff   
1   25.4              3313071.0  POINT (-71.21046 42.24782)  892a339a2dbffff   
2   25.1              3313071.0  POINT (-71.21653 42.25423)  892a339b5abffff   
3   32.0              3313071.0  POINT (-71.21653 42.25423)  892a339b5abffff   
4   45.7              3313071.0  POINT (-71.21432 42.25688)  892a339b5bbffff   

  has_time_window  height        lat        lng  package_id  \
0           False    10.7  42.249041 -71.210771         1.0   
1           False    12.7  42.247825 -71.210462         1.0   
2           False     8.6  42.254233 -71.216526         1.0   
3           False     1.0  42.254233 -71.216526         1.0   
4           False    21.6  42.256885 -71.214323         1.0   

   planned_service_time                                      route_id  \
0                  87.0  RouteID_00437423-5a8f-4fac-8efa-85264f0a3944   
1                 461.0  RouteID_8e86da60-9fe5-4021-8038-9f45cd81508c   
2                  31.0  RouteID_00437423-5a8f-4fac-8efa-85264f0a3944   
3                  82.0  RouteID_8e86da60-9fe5-4021-8038-9f45cd81508c   
4                  62.0  RouteID_00437423-5a8f-4fac-8efa-85264f0a3944   

  route_score station_code stop_id  time_of_day     type     volume  width  
0      Medium         DBO2      KN      33017.0  Dropoff   6016.075   17.3  
1        High         DBO2      LK      49745.0  Dropoff   5741.924   17.8  
2      Medium         DBO2      DP      33169.0  Dropoff   2676.664   12.4  
3        High         DBO2      IA      48477.0  Dropoff    944.000   29.5  
4      Medium         DBO2      VH      33279.0  Dropoff  22605.048   22.9

### Groupby Route and Lat/Lon


In [23]:
# # this is grouping to lat/lon level. Aka if there multiple stops at the same lat/lon they will be grouped together
# loc_route_df = (
#     route_df.groupby(["lat", "lng", "route_id"])
#     .agg(
#         {
#             "package_id": "sum",
#             "volume": ("mean", "sum"),
#             "width": ("mean",),
#             "height": ("mean",),
#             "planned_service_time": ("mean", "sum", "min", "max"),
#             "has_window": "max",
#             "status": "first",
#             "departure_datetime": "mean",
#             "has_window": "max",
#             # "city": "first",
#             # "city_zone": "first",
#             # "zone_id": "first",
#             "executor_capacity_cm3": "first",
#             "h3": "first",
#             **{col: "first" for col in tag_columns},
#         }
#     )
#     .reset_index()
# )


In [24]:
# # flatten the multi index
# new_names = []
# for col in loc_route_df.columns:
#     if not len(col[-1]) or "first" in col[1] or col[0] in tag_columns:
#         new_names.append(col[0])
#     else:
#         new_names.append("_".join(col))
# loc_route_df.columns = new_names


In [26]:
# loc_route_df.head()


In [12]:
route_df.to_pickle(
    "/Users/max/Downloads/shared_navish_dataframes_ALL_Boston_all_loc_route_w_tags.pkl",
    protocol=4,
)


## Plot the Hexagons


In [ ]:
# from geojson import Feature, FeatureCollection


In [ ]:
# def hexagons_dataframe_to_geojson(
#     df_hex, hex_id_field, geometry_field, value_field, file_output=None
# ):
#     # taken from https://medium.com/analytics-vidhya/how-to-create-a-choropleth-map-using-uber-h3-plotly-python-458f51593548
#     list_features = []

#     for i, row in df_hex.iterrows():
#         feature = Feature(
#             geometry=row[geometry_field],
#             id=row[hex_id_field],
#             properties={"value": row[value_field]},
#         )
#         list_features.append(feature)

#     feat_collection = FeatureCollection(list_features)

#     if file_output is not None:
#         with open(file_output, "w") as f:
#             json.dump(feat_collection, f)

#     else:
#         return feat_collection


In [ ]:
# loc_route_df["hex_shape"] = loc_route_df.h3.apply(h3_to_polygon)
# loc_route_df["lat_lng_route_id"] = loc_route_df.apply(
#     lambda x: "~".join((str(x.lat), str(x.lng), x.route_id)), axis=1
# )
# h3_grouped = (
#     loc_route_df.groupby("h3")
#     .agg(
#         {
#             "building_apartments": "sum",
#             "hex_shape": "first",
#             "planned_service_time_sum": "median",
#             "lat_lng_route_id": "count",
#         }
#     )
#     .reset_index()
# )


# h3_grouped["cliped_service_time"] = h3_grouped.planned_service_time_sum
# h3_grouped.loc[
#     h3_grouped["cliped_service_time"]
#     > h3_grouped["cliped_service_time"].quantile(0.95),
#     "cliped_service_time",
# ] = h3_grouped["cliped_service_time"].quantile(0.95)
# h3_grouped.loc[
#     h3_grouped["cliped_service_time"]
#     < h3_grouped["cliped_service_time"].quantile(0.05),
#     "cliped_service_time",
# ] = h3_grouped["cliped_service_time"].quantile(0.05)


# hex_geo_json = hexagons_dataframe_to_geojson(
#     h3_grouped,
#     hex_id_field="h3",
#     geometry_field="hex_shape",
#     value_field="cliped_service_time",
# )


In [ ]:
# h3_with_20 = set(h3_grouped.loc[h3_grouped.lat_lng_route_id > 20, "h3"].values)


In [ ]:
# res = {}
# for h, _df in loc_route_df.groupby("h3"):
#     res[h] = {}
#     for min in [2.5, 5, 10]:
#         if len(_df) > 20:
#             res[h][min] = sum(_df.planned_service_time_sum > (min * 60)) / len(
#                 _df.planned_service_time_sum
#             )
#         else:
#             res[h][min] = 0


In [ ]:
# q_df = pd.DataFrame.from_dict(res).T.reset_index()
# q_df.head()


index  2.5  5.0  10.0
0  892a3029093ffff  0.0  0.0   0.0
1  892a3064023ffff  0.0  0.0   0.0
2  892a3064027ffff  0.0  0.0   0.0
3  892a3064037ffff  0.0  0.0   0.0
4  892a30640a3ffff  0.0  0.0   0.0

In [ ]:
# import plotly.express as px
# import plotly.graph_objects as go

# fig = MapboxPlot()


# fig.add_trace(px.choropleth_mapbox(
#     h3_grouped,
#     geojson=hex_geo_json,
#     locations="h3",
#     color="cliped_service_time",
#     color_continuous_scale="Viridis",
#     # range_color=(0, 1),
#     mapbox_style="carto-positron",
#     zoom=7,
#     center={"lat": hexed_routes.lat.mean(), "lon": hexed_routes.lng.mean()},
#     opacity=0.7,
#     labels={"boxes"},
# ).data[0])


# # plot > 2.5
# for c in zip([2.5, 5, 10], [5, 10, 1000000]):

#     cut = loc_route_df.loc[
#         (loc_route_df.planned_service_time_sum > (c[0] * 60))
#         & (loc_route_df.planned_service_time_sum <= (c[1] * 60))
#     ]
#     fig.add_trace(
#         go.Densitymapbox(
#             lat=cut.lat,
#             lon=cut.lng,
#             z=cut.planned_service_time_sum,
#             radius=10,
#             name=f"{c}",
#         )
#     )

# fig.set_center(
#     lat=loc_route_df.lat.mean(),
#     lon=loc_route_df.lng.mean()
# )
# # fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0}, )  #height=1200, width=1800)
# # fig.write_html('h3_boston.html')
# fig.show()


In [ ]:
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# colorscale = [
#     "rgba(0, 147, 146, 0.2)",
#     "rgba(114, 170, 161, 1)",
#     "rgba(177, 199, 179, 1)",
#     "rgba(241, 234, 200, 1)",
#     "rgba(229, 185, 173, 1)",
#     "rgba(217, 137, 148, 1)",
#     "rgba(208, 88, 126, 1)",
# ]

colorscale = px.colors.sequential.Turbo.copy()
colorscale = colorscale[::-1]
colorscale[0] = "rgba(0, 0, 0, 0.0)"

fig = MapboxPlot()

fig = make_subplots(
    rows=1,
    cols=3,
    subplot_titles=(">2.5 min", ">5 min", " >10 min"),
    specs=[[{"type": "mapbox"}, {"type": "mapbox"}, {"type": "mapbox"}]],
)

for i, m in enumerate([2.5, 5, 10]):
    fig.add_trace(
        px.choropleth_mapbox(
            q_df,
            geojson=hex_geo_json,
            locations="index",
            color=m,
            color_continuous_scale=colorscale,
            range_color=(0, 1),
            # mapbox_style="carto-positron",
            zoom=7,
            center={"lat": hexed_routes.lat.mean(), "lon": hexed_routes.lng.mean()},
            opacity=0.7,
            labels={"boxes"},
        ).data[0],
        row=1,
        col=i + 1,
    )


fig.update_mapboxes(
    accesstoken=os.environ.get("MAPBOX_KEY"),
    style="mapbox://styles/max-schrader/cl6lhvrfw001516pkh3s6iv7l",
    bearing=0,
    zoom=10,
    center={"lat": hexed_routes.lat.mean(), "lon": hexed_routes.lng.mean()},
)

fig.update_layout(
    autosize=True,
    hovermode="closest",
    coloraxis={"colorscale": colorscale, "colorbar_title": "Probability"},
)


In [ ]:
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

fig = MapboxPlot()

fig = make_subplots(
    rows=1,
    cols=3,
    subplot_titles=(">2.5 min", ">5 min", " >10 min"),
    specs=[[{"type": "mapbox"}, {"type": "mapbox"}, {"type": "mapbox"}]],
    horizontal_spacing=0.05,
)

for i, c in enumerate(zip([2.5, 5, 10], [5, 10, 1e9])):

    fig.add_trace(
        px.choropleth_mapbox(
            q_df,
            geojson=hex_geo_json,
            locations="index",
            # color=m,
            # color_continuous_scale=colorscale,
            # range_color=(0, 1),
            # mapbox_style="carto-positron",
            zoom=7,
            center={"lat": hexed_routes.lat.mean(), "lon": hexed_routes.lng.mean()},
            opacity=0.7,
            labels={"boxes"},
        ).data[0],
        row=1,
        col=i + 1,
    )

    cut = loc_route_df.loc[
        (loc_route_df.planned_service_time_sum > (c[0] * 60))
        # & (loc_route_df.planned_service_time_sum <= (c[1] * 60))
    ]
    fig.add_trace(
        px.scatter_mapbox(
            cut,
            lat="lat",
            lon="lng",
            color="planned_service_time_sum",
            size="planned_service_time_sum",
            # col
            # locations="index",
            # color=m,
            # color_continuous_scale=colorscale,
            range_color=(2.5 * 60, 10 * 60),
            # # mapbox_style="carto-positron",
            # zoom=7,
            # center={"lat": hexed_routes.lat.mean(), "lon": hexed_routes.lng.mean()},
            # opacity=0.7,
            # labels={"boxes"},
        ).data[0],
        row=1,
        col=i + 1,
    )


fig.update_mapboxes(
    accesstoken=os.environ.get("MAPBOX_KEY"),
    style="mapbox://styles/max-schrader/cl6lhvrfw001516pkh3s6iv7l",
    bearing=0,
    zoom=10,
    center={"lat": hexed_routes.lat.mean(), "lon": hexed_routes.lng.mean()},
)

fig.update_layout(
    autosize=True,
    hovermode="closest",
    height=800,
    width=1400
    # coloraxis={
    #     "colorscale": colorscale,
    #     "colorbar_title": "Probability"
    # }
)


In [ ]:
# import plotly.figure_factory as ff


In [ ]:
# loc_route_df['lat_lng_route_id'] = loc_route_df.apply(lambda x: "~".join((str(x.lat), str(x.lng), x.route_id)), axis=1)
# h3_grouped = loc_route_df.groupby('h3').agg({'building_apartments': 'sum', 'hex_shape': 'first', 'planned_service_time_sum': 'mean', 'lat_lng_route_id': 'nunique'}).reset_index()


In [ ]:
# h3_grouped_big = h3_grouped.loc[h3_grouped.lat_lng_route_id > 10].copy()


In [ ]:
# h3_grouped_big


In [ ]:
# big_zone = loc_route_df.loc[loc_route_df.h3.isin(h3_grouped_big.h3)]


In [ ]:
# fig = ff.create_distplot(
#     [h3_grouped_big.planned_service_time_sum, h3_grouped.planned_service_time_sum, big_zone.planned_service_time_sum],
#     group_labels=['h3 mean distribution > 10 datapoints', 'h3 mean distribution all', 'single_zone'],
#     show_rug=False
# )


# # fig.update_layout(
# #     xaxis_range = [0, 500]
# # )
# fig.show()


In [ ]:
# import plotly.graph_objects as go


In [ ]:
# fig = go.Figure(
#     data=[
#         go.Scatter(
#             x=h3_grouped.lat_lng_route_id,
#             y=h3_grouped.planned_service_time_sum,
#             mode='markers'
#         )
#     ],
#     layout=dict(
#         xaxis_title='Number of deliveries in H3 hex',
#         yaxis_title="H3 Hex Average Service Time"
#     )
# )

# fig.write_html(
#     'num_deliveries_vs_service_time.html'
# )


In [ ]:
# h3_grouped.loc[h3_grouped.lat_lng_route_id > 20, 'h3'].sample(1).values[0]


In [ ]:
# random_big_zone = '892a3065507ffff'

# fig = go.Figure(
#     data=[
#         go.Histogram(
#             x=h3_grouped.planned_service_time_sum,
#             name="All H3",
#             histnorm='probability',
#             opacity=0.5,
#             bingroup='group'
#         ),
#         go.Histogram(
#             x=h3_grouped.loc[h3_grouped.lat_lng_route_id > 20].planned_service_time_sum,
#             name="H3 w/ >20 Deliveries",
#             histnorm='probability',
#             opacity=0.5,
#             bingroup='group'
#         ),
#         go.Histogram(
#             x=loc_route_df.loc[loc_route_df.h3 == random_big_zone].planned_service_time_sum,
#             name="Intra-hex variance for zone w/ >20",
#             histnorm='probability',
#             opacity=0.5,
#             bingroup='group'
#         ),
#     ],
#     layout=dict(
#         xaxis_title='Average Service Time',
#         yaxis_title="Probability",
#         barmode='overlay'
#     )
# )

# fig.data = fig.data[::-1]
# fig.write_html(
#     'h3_hist.html'
# )
# fig.show()
